# Loading data from mysql to pandas

In [3]:
import os
import pymysql
import pandas as pd

host = os.getenv('MYSQL_HOST')
port = os.getenv('MYSQL_PORT')
user = os.getenv('MYSQL_USER')
password = '7dc41992'
database = os.getenv('MYSQL_DATABASE')

conn = pymysql.connect(
    host=host,
    port=int(3306),
    user="root",
    passwd=password,
    db="twitterdb",
    charset='utf8mb4')

In [4]:
query = "SELECT * FROM user"
user_df = pd.read_sql_query(query, conn)

In [5]:
user_df.head(10)

user_id                 user_created_at   screen_name friends_count  \
0    1186.0  Sun Jul 16 06:53:48 +0000 2006  chrismessina          5917   
1    1585.0  Sun Jul 16 21:38:36 +0000 2006  dhinchcliffe          5014   
2    1688.0  Mon Jul 17 01:21:51 +0000 2006    ifindkarma         95142   
3   17913.0  Thu Nov 23 12:44:11 +0000 2006   ryanmcraver           682   
4   29283.0  Wed Nov 29 01:51:08 +0000 2006     tigerbeat         11377   
5   61753.0  Tue Dec 12 21:18:27 +0000 2006        kdeiss          1042   
6   69053.0  Thu Dec 14 23:41:16 +0000 2006          Aine          3534   
7  483223.0  Wed Jan 03 06:19:55 +0000 2007      itsWanda          7064   
8  666913.0  Fri Jan 19 19:13:08 +0000 2007       c4chaos          6414   
9  730473.0  Tue Jan 30 04:22:51 +0000 2007      bvergara           913   

  statuses_count followers_count  
0          54185          104195  
1          56220           56727  
2          71058          198569  
3          21403            1966  
4         491810           10346  
5          16566             611  
6         245958            4753  
7         588737            7335  
8          72062            5893  
9          26371            1320

In [52]:
len(user_df)

23199

In [6]:
query = "SELECT * FROM tweet"
tweet_df = pd.read_sql_query(query, conn)
tweet_df.created_at = pd.to_datetime(tweet_df.created_at)

In [53]:
len(tweet_df)

23123

In [7]:
tweet_df.head(10)

id                      created_at  \
0  1.257823e+18  Wed May 06 00:01:19 +0000 2020   
1  1.257823e+18  Wed May 06 00:01:19 +0000 2020   
2  1.257823e+18  Wed May 06 00:01:20 +0000 2020   
3  1.257823e+18  Wed May 06 00:01:20 +0000 2020   
4  1.257823e+18  Wed May 06 00:01:20 +0000 2020   
5  1.257823e+18  Wed May 06 00:01:20 +0000 2020   
6  1.257823e+18  Wed May 06 00:01:20 +0000 2020   
7  1.257823e+18  Wed May 06 00:01:20 +0000 2020   
8  1.257823e+18  Wed May 06 00:01:20 +0000 2020   
9  1.257823e+18  Wed May 06 00:01:20 +0000 2020   

                                              source  \
0  <a href="http://twitter.com" rel="nofollow">Tw...   
1  <a href="http://twitter.com/download/iphone" r...   
2  <a href="https://mobile.twitter.com" rel="nofo...   
3  <a href="http://twitter.com/download/iphone" r...   
4  <a href="http://twitter.com/download/iphone" r...   
5  <a href="http://twitter.com/download/android" ...   
6  <a href="http://twitter.com/download/iphone" r...   
7  <a href="http://twitter.com/download/android" ...   
8  <a href="http://twitter.com/download/android" ...   
9  <a href="https://mobile.twitter.com" rel="nofo...   

                                                text  sentiment       user_id  \
0      ...it's just not the same anymore... #COVID19          0  5.359793e+08   
1  RT : Saudi Arabia may be an uneected beneficia...          0  8.348396e+17   
2  RT : Tomorrow will ee the mainstream media rol...          0  1.158475e+18   
3  MAKE SURE LAURA INGRAHAM SEE S THIS PLEASE WAT...          1  1.198760e+18   
4  RT : As an Emergency Doctor who takes responsi...          0  5.554319e+08   
5  RT : So they ve been telling us all along abou...         -1  2.512833e+08   
6  RT : Why are you using , Ted? You could just s...          0  2.735614e+09   
7  RT : In the midst of the #COVID19 the Joint SD...          1  1.150587e+18   
8  "Coronavirus: Human trials for eerimental vacc...          0  9.641790e+17   
9  RT : Strong words from . He says China s handl...         -1  3.172204e+07   

  place_id  
0     None  
1     None  
2     None  
3     None  
4     None  
5     None  
6     None  
7     None  
8     None  
9     None

# Sentiment Analysis

In [84]:
s = tweet_df.sentiment.value_counts()
sentiment_df = pd.DataFrame({'sentiment':s.index, 'count':s.values})

import plotly.graph_objects as go
sentiment=['positive', 'neutral', 'negative']

fig = go.Figure([go.Bar(x=sentiment, y=list(sentiment_df['count']))])
fig.show()

# Plotting timeline of tweet volume

In [75]:
# Using plotly.express
import plotly.express as px
import pandas as pd
g = tweet_df.groupby(tweet_df.created_at.map(lambda t: t.minute))
g = g.agg(['count'])['created_at']['count']

timeline_df = pd.DataFrame({'time':g.index, 'count':g.values})
fig = px.line(timeline_df, x='time', y='count')
fig.show()

# Number of tweets ranked by countries

In [85]:
import plotly.express as px
query = 'SELECT * from tweet t INNER JOIN place p ON t.place_id = p.place_id'
d = pd.read_sql_query(query, conn)

s = d.country.value_counts()
country_df = pd.DataFrame({'country':s.index, 'count':s.values})

fig = px.pie(country_df[:10], values='count', names='country', title='Share of tweets by country')
fig.show()

# Find popular hashtags

In [161]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.width', None)
pd.set_option('display.max_colwidth', -1)

In [88]:
from pymongo import MongoClient

myclient = MongoClient()
mydb = myclient["tweetbase"]
tweets = mydb["tweets"]

In [132]:
entities = tweets.find({ }, {"entities.hashtags": 1})

In [133]:
hashtag_list = []
for entity in entities:
    try:
        if len(entity['entities']['hashtags']) > 0:
            hashtag_list.append(entity['entities']['hashtags'])
    except:
        pass

In [136]:
flat_hashtags = []
for hashtags in hashtag_list:
    for h in hashtags:
        flat_hashtags.append(h['text'])
    

In [140]:
flat_hashtags = [x.lower() for x in flat_hashtags]

In [145]:
from collections import Counter
hashtag_counts = dict(Counter(flat_hashtags))

In [152]:
data = {'hashtags': list(hashtag_counts.keys()), 'count': list(hashtag_counts.values())}

In [153]:
hashtag_df = pd.DataFrame.from_dict(data)

In [162]:
hashtag_df.sort_values(by=['count'], ascending=False)

hashtags  count
3      covid19                                            98459
2      coronavirus                                        42929
6      stayhome                                           8327 
28     lockdown                                           3645 
45     covidー19                                           2958 
25     covid                                              2917 
18     givingtuesdaynow                                   2404 
124    pandemic                                           2262 
10     china                                              1597 
7      staysafe                                           1325 
337    trump                                              1320 
53     breaking                                           1312 
22272  recall                                             1234 
36     indiafightscorona                                  1167 
285    coronaviruspandemic                                1113 
49     fakenews                                           1095 
92     iran                                               1073 
16     covidiot                                           1060 
464    sarscov2                                           962  
83     coronavirusoutbreak                                953  
234    magats                                             948  
59     stayhomestaysafe                                   913  
24     handhygiene                                        905  
64     cincodemayo                                        834  
222    superm                                             794  
336    stayathome                                         794  
132    usnscomfort                                        791  
220    stayhomewithsuperm                                 789  
96     corona                                             763  
110    covid_19                                           743  
221    baekhyun                                           691  
332    covidiots                                          662  
131    givingtuesday                                      637  
4190   trump2020                                          636  
405    socialdistancing                                   627  
370    covid2019                                          624  
100    usa                                                588  
218    pakistan                                           486  
450    israel                                             471  
1593   cdnpoli                                            448  
242    playaparttogether                                  443  
102    quarantine                                         441  
777    economy                                            435  
104    nyc                                                434  
84     dhookudu                                           430  
5      liquorshop                                         419  
8      extraction                                         415  
239    telangana                                          413  
179    mentalhealth                                       396  
23     wuhan                                              393  
1165   us                                                 385  
17     worldhandhygieneday                                385  
113    vaccine                                            376  
37     fearlessathome                                     371  
369    watch                                              363  
136    uk                                                 360  
14423  rickbright                                         356  
98     movid14                                            346  
1031   italy                                              331  
114    india                                              326  
7900   policeodu                                          324  
7899   vijay                                              318  
463    remdesivi